In [0]:
import numpy as np
import plotly.graph_objects

from ipywidgets import SelectionSlider


In [2]:
mydefault = plotly.graph_objects.layout.Template()
mydefault.layout.xaxis.showgrid = False
mydefault.layout.yaxis.showgrid = False
mydefault.layout.xaxis.showline = True
mydefault.layout.yaxis.showline = True
mydefault.layout.hovermode = False
mydefault.layout.dragmode = "pan"
mydefault.layout.scene.hovermode = False
mydefault.layout.xaxis.showspikes = False
mydefault.layout.yaxis.showspikes = False
mydefault.layout.scene.xaxis.showspikes = False
mydefault.layout.scene.yaxis.showspikes = False
mydefault.layout.scene.zaxis.showspikes = False
plotly.io.templates["mydefault"] = mydefault
plotly.io.templates.default = "mydefault"


In [3]:
def plotly_function3d(f, x_range, y_range, **options):
    useroptions = options
    options = dict(showscale=False, hoverinfo="none", contours_x_highlight=False, 
                   contours_y_highlight=False, contours_z_highlight=False)
    options.update(useroptions)
    plotpoints = options.pop("plotpoints", 81)
    try:
        plotpointsx, plotpointsy = plotpoints
    except:
        plotpointsx = plotpointsy = plotpoints
    color = options.pop("color", "lightblue")
    options.setdefault("colorscale", [[0, color], [1, color]])
    x, xmin, xmax = x_range
    y, ymin, ymax = y_range
    f0 = fast_float(f, x, y)
    x = np.linspace(float(xmin), float(xmax), plotpointsx)
    y = np.linspace(float(ymin), float(ymax), plotpointsy)
    x, y = np.meshgrid(x, y)
    xy = np.array([x.flatten(), y.flatten()]).transpose()
    z = np.array([f0(x0, y0) for x0, y0 in xy]).reshape(plotpointsy, plotpointsx)
    return plotly.graph_objects.Surface(x=x, y=y, z=z, **options)


**Learning goals:**

- Know how to visualize the graph of a function $f(X, Y)$. 


In [6]:
def graph_surface_interactive(f, x_range, y_range, **options):
    x, xmin, xmax = x_range
    y, ymin, ymax = y_range
    zmin = options.get("zmin", 0)
    zmax = options.get("zmax", 12)
    f = fast_float(f, x, y)
    x = np.random.uniform(xmin, xmax, 2001)
    x[0] = xmin - 1
    y = np.random.uniform(ymin, ymax, 2001)
    z = np.array([f(X, Y) for X,Y in zip(x, y)])

    fig = plotly.graph_objects.FigureWidget()
    fig.layout.margin = dict(t=10, b=10, r=10, l=10)
    fig.layout.showlegend = True
    fig.layout.legend.y = 0.9
    fig.layout.legend.font.size = 16
    #fig.layout.scene.domain.x = (0.3, 1)
    fig.layout.scene.xaxis.title.text = "X"
    fig.layout.scene.yaxis.title.text = "Y"
    fig.layout.scene.zaxis.title.text = "Z"
    fig.layout.scene.xaxis.range = (xmin, xmax)
    fig.layout.scene.yaxis.range = (ymin, ymax)
    fig.layout.scene.zaxis.range = (zmin, zmax)
    fig.layout.scene.aspectmode = "cube"

    fig.add_scatter3d(name="Points on XY-plane", mode="markers", 
                      marker_color="red", marker_size=2)
    on_plane = fig.data[-1]
    fig.add_scatter3d(name="Points on graph", mode="markers", 
                      marker_color="blue", marker_size=2)
    on_graph = fig.data[-1]

    options = list(range(17)) + [50, 100, 200, 400, 800, 2000, 4000]
    options = [(f"{(n + 1) // 2}{' '*(n % 2)}", n) for n in options]
    @interact(numpoints=SelectionSlider(options=options, continuous_update=false, 
                                        description="Points:"))
    def update(numpoints):
        n1 = (numpoints + 1) // 2 + 1
        n2 = numpoints // 2 + 1
        with fig.batch_update():
            on_plane.x = x[:n1]
            on_plane.y = y[:n1]
            on_plane.z = np.zeros(n1)
            on_graph.x = x[:n2]
            on_graph.y = y[:n2]
            on_graph.z = z[:n2]

    return fig


In [9]:
f(x, y) = 0.5 + sin(x/1.5)*cos(y/2) + 1 - 2*cos(x/3)*sin(y/5) + 2
graph_surface_interactive(f, (x, -6, 6), (y, -6, 6))


Interactive function <function graph_surface_interactive.<locals>.update at 0x7fec21927730> with 1 widget
  nu…

FigureWidget({
    'data': [{'marker': {'color': 'red', 'size': 2},
              'mode': 'markers',
         …

In [8]:
f(x, y) = 0.5 + sin(x/1.5)*cos(y/2) + 1 - 2*cos(x/3)*sin(y/5) + 2
fig = plotly.graph_objects.Figure()
fig.layout.margin = dict(t=10, b=10, r=10, l=10)
fig.layout.scene.xaxis.title.text = "X"
fig.layout.scene.yaxis.title.text = "Y"
fig.layout.scene.zaxis.title.text = "Z"
fig.layout.scene.xaxis.range = (-6, 6)
fig.layout.scene.yaxis.range = (-6, 6)
fig.layout.scene.zaxis.range = (0, 12)
fig.layout.scene.aspectmode = "cube"
fig.add_trace(plotly_function3d(f, (x, -6, 6), (y, -6, 6)))
fig


**Conclusions:**

1. The graph of a function $Z = f(X, Y)$ is a ***surface*** in 3-D space ($XYZ$-space). 
